In [48]:
import pandas as pd
import plotly.express as px
from collections import defaultdict
from tqdm import tqdm
import numpy as np
import json

In [93]:
graph_data_path_root = '../GraphData'
output_root_dir = '../HetGNN/ProcessedData'

## Meta Files

In [50]:
id_service_df = pd.read_csv(f'{graph_data_path_root}/id_service.csv', index_col=0)
id_service_df

Service
0               ts-order-service
1             ts-station-service
2             ts-travel2-service
3          ts-ticketinfo-service
4               ts-basic-service
5               ts-route-service
6               ts-train-service
7               ts-price-service
8         ts-order-other-service
9                ts-seat-service
10             ts-config-service
11               ts-food-service
12           ts-food-map-service
13             ts-travel-service
14            ts-execute-service
15          ts-assurance-service
16     ts-inside-payment-service
17            ts-payment-service
18           ts-contacts-service
19               ts-auth-service
20  ts-verification-code-service
21     ts-preserve-other-service
22           ts-security-service
23               ts-user-service
24       ts-notification-service
25           ts-delivery-service
26             ts-cancel-service
27           ts-preserve-service
28   ts-admin-basic-info-service
29       ts-admin-travel-service
30            ts-consign-service
31      ts-consign-price-service
32             ts-rebook-service
33        ts-travel-plan-service
34         ts-route-plan-service

In [51]:
id_url_temp_df = pd.read_csv(f'{graph_data_path_root}/id_url+temp.csv', index_col=0)
id_url_temp_df

EventTemplate
0     draw back payment, userId: <:UNIQUE_ID:>, mone...
1                  [Draw Back Money] Draw back money...
2     [Cancel Order Service] Delay Process，Wrong Can...
3                      [Cancel Order] Order <:*:> <:*:>
4                     [Get Order By Id] Order Id: <:*:>
...                                                 ...
1508  {POST}/api/v1/routeplanservice/routePlan/minSt...
1509  {GET}/api/v1/routeservice/routes/{startId}/{te...
1510           {POST}/api/v1/travelservice/trips/routes
1511          {POST}/api/v1/travel2service/trips/routes
1512  /api/v1/consignpriceservice/consignprice/0.0/f...

[1513 rows x 1 columns]

In [52]:
id_url_type_df = pd.read_csv(f'{graph_data_path_root}/id_url+type.csv', index_col=0)
id_url_type_df

Temp  Type                                            Content
0        0     4  draw back payment, userId: <:UNIQUE_ID:>, mone...
1        1     4               [Draw Back Money] Draw back money...
2        2     4  [Cancel Order Service] Delay Process，Wrong Can...
3        3     4                   [Cancel Order] Order <:*:> <:*:>
4        4     4                  [Get Order By Id] Order Id: <:*:>
...    ...   ...                                                ...
1873  1511     3  Client Response {POST}/api/v1/travel2service/t...
1874  1512     0  Server Request /api/v1/consignpriceservice/con...
1875  1512     2  Server Response /api/v1/consignpriceservice/co...
1876  1512     1  Client Request /api/v1/consignpriceservice/con...
1877  1512     3  Client Response /api/v1/consignpriceservice/co...

[1878 rows x 3 columns]

In [53]:
id_url_type_df.Type.unique()

array([4, 0, 2, 1, 3, 5, 6, 7])

In [54]:
id_url_temp_df.iloc[1512].values

array(['/api/v1/consignpriceservice/consignprice/0.0/false'], dtype=object)

In [55]:
id_url_type_df.iloc[1874].values, id_url_type_df.iloc[1875].values, id_url_type_df.iloc[1876].values, id_url_type_df.iloc[1877].values

(array([1512, 0,
        'Server Request /api/v1/consignpriceservice/consignprice/0.0/false'],
       dtype=object),
 array([1512, 2,
        'Server Response /api/v1/consignpriceservice/consignprice/0.0/false'],
       dtype=object),
 array([1512, 1,
        'Client Request /api/v1/consignpriceservice/consignprice/0.0/false'],
       dtype=object),
 array([1512, 3,
        'Client Response /api/v1/consignpriceservice/consignprice/0.0/false'],
       dtype=object))

## Process Files

In [100]:
import json
with open(f'{graph_data_path_root}/process0.jsons', 'r') as fin:
    line = fin.readline()
sample = json.loads(line)
sample.keys()

dict_keys(['edge_index', 'edge_attr', 'node_info', 'trace_id', 'trace_bool', 'error_trace_type'])

In [101]:
for k in sample.keys():
    if isinstance(sample[k], list):
        print(f'{k} size: {len(sample[k])}')
    else:
        print(f'{k}: {sample[k]}')

edge_index size: 962
edge_attr size: 962
node_info size: 841
trace_id: 007efb9578bc4f1ab3eab03cb5188af5.38.16292558869030095
trace_bool: True
error_trace_type: normal


In [102]:
import numpy as np
np.unique(np.array(sample['edge_index']).flatten()).max()

840

In [103]:
set(sample['edge_attr'])

{0, 1, 2}

In [107]:
sample['node_info'][:10]
# for i in range(np.array(sample['node_info']).shape[1]):
#     print(f"{i}: {np.unique(np.array(sample['node_info'])[:, i])}")


[[1460.0, 13, -1, 0, 0, 0, 1666],
 [1460.0, 13, -1, 922, 2, 0, 1667],
 [502.0, 13.0, -1, 2.0, 4, 0.0, 502],
 [1364.0, 13.0, 13, 3.0, 1, 1.0, 1375],
 [1364.0, 13.0, 13, 10.0, 1, 2.0, 1375],
 [1364.0, 13.0, 13, 10.0, 3, 1.0, 1376],
 [44.0, 13.0, -1, 10.0, 4, 0.0, 44],
 [1364.0, 13.0, 13, 17.0, 3, 2.0, 1376],
 [44.0, 13.0, -1, 17.0, 4, 0.0, 44],
 [1388.0, 13.0, 13, 18.0, 5, 3.0, 1448]]

### Trace Info Overview

In [56]:
from collections import defaultdict
from tqdm import tqdm

In [57]:
trace_info = defaultdict(list)

for idx in range(0, 9):
    with open(f'{graph_data_path_root}/process{idx}.jsons', 'r') as fin:
        for line in tqdm(fin.readlines()):
            trace = json.loads(line)
            trace_info['trace_id'].append(trace['trace_id'])
            trace_info['trace_bool'].append(trace['trace_bool'])
            trace_info['error_trace_type'].append(trace['error_trace_type'])
            trace_info['process_idx'].append(idx)

trace_info_df = pd.DataFrame(trace_info)
trace_info_df

100%|██████████| 14719/14719 [00:04<00:00, 3330.16it/s]


trace_id  trace_bool  \
0       007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...        True   
1       007efb9578bc4f1ab3eab03cb5188af5.38.1629255918...        True   
2       007efb9578bc4f1ab3eab03cb5188af5.38.1629255966...        True   
3       007efb9578bc4f1ab3eab03cb5188af5.38.1629255999...        True   
4       007efb9578bc4f1ab3eab03cb5188af5.38.1629256047...        True   
...                                                   ...         ...   
132480  ffc3e79734424b65942466e0d8d432e2.46.1628705867...       False   
132481  ffc3e79734424b65942466e0d8d432e2.47.1628705858...       False   
132482  ffc3e79734424b65942466e0d8d432e2.47.1628705861...       False   
132483  ffc3e79734424b65942466e0d8d432e2.47.1628705865...       False   
132484  ffc3e79734424b65942466e0d8d432e2.47.1628705868...       False   

       error_trace_type  process_idx  
0                normal            0  
1                normal            0  
2                normal            0  
3                normal            0  
4                normal            0  
...                 ...          ...  
132480           F04-02            8  
132481           F04-02            8  
132482           F04-02            8  
132483           F04-02            8  
132484           F04-02            8  

[132485 rows x 4 columns]

In [98]:
trace_info_df.error_trace_type.unique()

array(['normal', 'F02-06', 'F07-04', 'F07-05', 'F04-06', 'F06-05',
       'F01-03', 'F05-01', 'F12-01', 'F01-02', 'F05-03', 'F06-04',
       'F05-02', 'F14-03', 'F10-02', 'F03-07', 'F03-08', 'F13-03',
       'F07-02', 'F02-04', 'F11-02', 'F11-01', 'F04-01', 'F08-01',
       'F10-01', 'F10-03', 'F09-01', 'F09-03', 'F02-01', 'F02-02',
       'F02-03', 'F04-03', 'F13-05', 'F07-01', 'F08-04', 'F14-02',
       'F08-02', 'F12-03', 'F03-03', 'F04-07', 'F04-08', 'F06-01',
       'F06-02', 'F06-03', 'F13-04', 'F13-01', 'F01-01', 'F08-05',
       'F01-04', 'F01-05', 'F11-05', 'F11-04', 'F11-03', 'F08-03',
       'F03-01', 'F05-05', 'F07-03', 'F09-02', 'F03-04', 'F04-05',
       'F03-06', 'F03-05', 'F12-05', 'F05-04', 'F02-05', 'F03-02',
       'F14-01', 'F12-02', 'F13-02', 'F04-04', 'F04-02'], dtype=object)

In [62]:
# trace_info_df['trace_id'] = trace_info_df['trace_id'].apply(lambda x: trace_id_idx[x])
trace_info_df.to_csv(f'../HetGNN/ProcessedData/trace_info.csv', index=False)


In [64]:
109151 * 0.6

65490.6

In [29]:
px.histogram(trace_info_df, x='trace_bool', color='process_idx')

In [30]:
px.histogram(trace_info_df, x=['error_trace_type'], color='process_idx')

## Edge Info

In [7]:
import json
edge_details = defaultdict(list)
for idx in range(0, 9):
    with open(f'{graph_data_path_root}/process{idx}.jsons', 'r') as fin:
        for line in tqdm(fin.readlines()):
            trace = json.loads(line)
            node_info = trace['node_info']
            for (src_id, dst_id), edge_type in zip(trace['edge_index'], trace['edge_attr']):
                edge_details['src_id'].append(src_id)
                edge_details['src_type'].append(node_info[src_id][4])
                edge_details['dst_id'].append(dst_id)
                edge_details['dst_type'].append(node_info[dst_id][4])
                edge_details['edge_type'].append(edge_type)
                edge_details['trace_id'].append(trace['trace_id'])
            break
    break
edge_details_df = pd.DataFrame(edge_details)
edge_details_df

  0%|          | 0/14721 [00:00<?, ?it/s]


src_id  src_type  dst_id  dst_type  edge_type  \
0         0         0       2         4          0   
1         2         4       3         1          0   
2         3         1       4         1          0   
3         4         1       5         3          0   
4         5         3       6         4          0   
..      ...       ...     ...       ...        ...   
957     817         2     744         3          2   
958     822         2      69         3          2   
959     827         2      70         3          2   
960     832         2     700         3          2   
961     837         2      73         3          2   

                                              trace_id  
0    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
1    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
2    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
3    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
4    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
..                                                 ...  
957  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
958  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
959  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
960  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
961  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  

[962 rows x 6 columns]

In [82]:
edge_details_df[['src_id', 'dst_id']].values.flatten().max()

862

In [8]:
edge_details_df.groupby('edge_type')[['trace_id']].count()

trace_id
edge_type          
0               718
1               122
2               122

In [9]:
edge_details_df.src_id.max(), edge_details_df.dst_id.max()

(840, 840)

In [10]:
sample_edges = edge_details_df[edge_details_df['trace_id'] == '007efb9578bc4f1ab3eab03cb5188af5.38.16292558869030095']
sample_edges

src_id  src_type  dst_id  dst_type  edge_type  \
0         0         0       2         4          0   
1         2         4       3         1          0   
2         3         1       4         1          0   
3         4         1       5         3          0   
4         5         3       6         4          0   
..      ...       ...     ...       ...        ...   
957     817         2     744         3          2   
958     822         2      69         3          2   
959     827         2      70         3          2   
960     832         2     700         3          2   
961     837         2      73         3          2   

                                              trace_id  
0    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
1    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
2    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
3    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
4    007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
..                                                 ...  
957  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
958  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
959  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
960  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
961  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  

[962 rows x 6 columns]

In [49]:
sample_edges[sample_edges['src_id'] == 237]

src_id  src_type  dst_id  dst_type  edge_type  \
211     237         4     233         2          0   

                                              trace_id  
211  007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...

In [11]:

node_type_df = pd.concat([sample_edges[['src_id', 'src_type']].rename(columns={'src_id': 'node_id', 'src_type': 'node_type'}),
sample_edges[['dst_id', 'dst_type']].rename(columns={'dst_id': 'node_id', 'dst_type': 'node_type'})]).drop_duplicates()

node_type_dict = {}

[node_type_dict.update(d) for d in node_type_df.apply(lambda x: {x[0]:x[1]}, axis=1).values]
node_type_dict


{0: 0,
 2: 4,
 3: 1,
 4: 1,
 5: 3,
 6: 4,
 7: 3,
 8: 4,
 9: 5,
 10: 1,
 11: 1,
 12: 3,
 13: 1,
 14: 1,
 15: 1,
 16: 1,
 17: 3,
 18: 3,
 19: 1,
 20: 3,
 21: 3,
 22: 1,
 23: 3,
 24: 3,
 25: 1,
 26: 1,
 27: 3,
 28: 1,
 29: 1,
 30: 3,
 31: 3,
 32: 1,
 33: 1,
 34: 3,
 35: 3,
 36: 1,
 37: 1,
 38: 3,
 39: 3,
 40: 1,
 41: 3,
 42: 1,
 43: 1,
 44: 3,
 45: 1,
 46: 3,
 47: 3,
 48: 1,
 49: 1,
 50: 3,
 51: 3,
 52: 1,
 53: 1,
 54: 3,
 55: 1,
 56: 3,
 57: 1,
 58: 3,
 59: 1,
 60: 1,
 61: 3,
 62: 3,
 63: 1,
 64: 3,
 65: 1,
 66: 3,
 67: 1,
 68: 3,
 69: 3,
 70: 3,
 71: 1,
 72: 3,
 73: 3,
 74: 0,
 76: 1,
 77: 4,
 78: 3,
 79: 0,
 81: 1,
 82: 4,
 83: 4,
 84: 3,
 85: 0,
 87: 4,
 88: 5,
 89: 0,
 91: 1,
 92: 4,
 93: 3,
 94: 0,
 96: 1,
 97: 4,
 98: 4,
 99: 3,
 100: 0,
 102: 5,
 103: 4,
 104: 0,
 106: 4,
 107: 5,
 108: 0,
 110: 4,
 111: 5,
 112: 0,
 114: 1,
 115: 4,
 116: 3,
 117: 0,
 119: 4,
 120: 5,
 121: 0,
 123: 5,
 124: 4,
 125: 0,
 127: 4,
 128: 5,
 129: 0,
 131: 4,
 132: 1,
 133: 3,
 134: 0,
 136: 4,
 137:

In [12]:
import networkx as nx

G = nx.from_pandas_edgelist(sample_edges, source='src_id', target='dst_id', edge_attr='edge_type')
G

In [13]:
G_node_types = [node_type_dict[n] for n in G.nodes]
G_node_types[:10]

[0, 4, 1, 1, 3, 4, 3, 4, 5, 1]

In [14]:
N=len(G.nodes)
N

841

In [50]:
import igraph as ig

Edges = list(G.edges)
iG = ig.Graph(Edges, directed=True)
iG

In [51]:
labels = []
group = []
for node_id, node_type in zip(G.nodes, G_node_types):
    labels.append(node_id)
    group.append(node_type)

In [52]:
layt=iG.layout('kk', dim=3)

In [53]:
layt[0]

[1.2785312583098368e-15, 0.0, -10.44]

In [54]:
Xn=[layt[k][0] for k in range(N)]# x-coordinates of nodes
Yn=[layt[k][1] for k in range(N)]# y-coordinates
Zn=[layt[k][2] for k in range(N)]# z-coordinates
Xe=[]
Ye=[]
Ze=[]
for e in Edges:
    Xe+=[layt[e[0]][0],layt[e[1]][0], None]# x-coordinates of edge ends
    Ye+=[layt[e[0]][1],layt[e[1]][1], None]
    Ze+=[layt[e[0]][2],layt[e[1]][2], None]

In [55]:
import chart_studio.plotly as py
import plotly.graph_objs as go
import urllib3

trace1=go.Scatter3d(x=Xe,
               y=Ye,
               z=Ze,
               mode='lines',
               line=dict(color='rgb(125,125,125)', width=1),
               hoverinfo='none'
               )

trace2=go.Scatter3d(x=Xn,
               y=Yn,
               z=Zn,
               mode='markers',
               name='actors',
               marker=dict(symbol='circle',
                             size=6,
                             color=group,
                             colorscale='Viridis',
                             line=dict(color='rgb(50,50,50)', width=0.5)
                             ),
               text=labels,
               hoverinfo='text'
               )

axis=dict(showbackground=False,
          showline=False,
          zeroline=False,
          showgrid=False,
          showticklabels=False,
          title=''
          )

layout = go.Layout(
        #  title="Network of coappearances of characters in Victor Hugo's novel<br> Les Miserables (3D visualization)",
         width=1000,
         height=1000,
         showlegend=False,
         scene=dict(
             xaxis=dict(axis),
             yaxis=dict(axis),
             zaxis=dict(axis),
        ),
     margin=dict(
        t=100
    ),
    hovermode='closest',
    # annotations=[
    #        dict(
    #        showarrow=False,
    #         # text='labels',
    #         # xref='paper',
    #         # yref='paper',
    #         x=0,
    #         y=0.1,
    #         xanchor='left',
    #         yanchor='bottom',
    #         font=dict(
    #         size=14
    #         )
    #         )
    #     ],    
)

In [56]:
data=[trace1, trace2]
fig=go.Figure(data=data, layout=layout)
fig
# py.iplot(fig, filename='sample_trace_graph', )

### Process Edges

In [5]:
import json
edge_details = defaultdict(list)
for idx in range(0, 9):
    with open(f'{graph_data_path_root}/process{idx}.jsons', 'r') as fin:
        for line in tqdm(fin.readlines()):
            trace = json.loads(line)
            node_info = trace['node_info']
            for (src_id, dst_id), edge_type in zip(trace['edge_index'], trace['edge_attr']):
                edge_details['src_id'].append(src_id)
                edge_details['src_type'].append(node_info[src_id][4])
                edge_details['dst_id'].append(dst_id)
                edge_details['dst_type'].append(node_info[dst_id][4])
                edge_details['edge_type'].append(edge_type)
                edge_details['trace_id'].append(trace['trace_id'])
edge_details_df = pd.DataFrame(edge_details)
edge_details_df

100%|██████████| 14719/14719 [00:17<00:00, 821.37it/s] 


src_id  src_type  dst_id  dst_type  edge_type  \
0              0         0       2         4          0   
1              2         4       3         1          0   
2              3         1       4         1          0   
3              4         1       5         3          0   
4              5         3       6         4          0   
...          ...       ...     ...       ...        ...   
29677741      14         4      15         4          0   
29677742      15         4      16         3          0   
29677743      16         3      17         4          0   
29677744      17         4      18         4          0   
29677745      18         4       1         2          0   

                                                   trace_id  
0         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
1         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
2         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
3         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
4         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...  
...                                                     ...  
29677741  ffc3e79734424b65942466e0d8d432e2.47.1628705868...  
29677742  ffc3e79734424b65942466e0d8d432e2.47.1628705868...  
29677743  ffc3e79734424b65942466e0d8d432e2.47.1628705868...  
29677744  ffc3e79734424b65942466e0d8d432e2.47.1628705868...  
29677745  ffc3e79734424b65942466e0d8d432e2.47.1628705868...  

[29677746 rows x 6 columns]

In [7]:
trace_id_idx = {i:idx for idx, i in enumerate(edge_details_df['trace_id'].unique())}
trace_id_idx

{'007efb9578bc4f1ab3eab03cb5188af5.38.16292558869030095': 0,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292559185490209': 1,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292559661930463': 2,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292559997970635': 3,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292560476751017': 4,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292560535851045': 5,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292560561031055': 6,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292560682031129': 7,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292560768031179': 8,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292561172141561': 9,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292561219941605': 10,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292561605952065': 11,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292561764452363': 12,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292561905452533': 13,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292561982742623': 14,
 '007efb9578bc4f1ab3eab03cb5188af5.38.16292562048462765': 15,
 '007efb9578bc4f1a

In [9]:
with open(f'{output_root_dir}/trace_id_idx.json', 'w') as fout:
    fout.write(json.dumps(trace_id_idx))
    fout.write('\n')

In [10]:
edge_details_df['trace_id'] = edge_details_df['trace_id'].apply(lambda x: trace_id_idx[x])
edge_details_df

src_id  src_type  dst_id  dst_type  edge_type  trace_id
0              0         0       2         4          0         0
1              2         4       3         1          0         0
2              3         1       4         1          0         0
3              4         1       5         3          0         0
4              5         3       6         4          0         0
...          ...       ...     ...       ...        ...       ...
29677741      14         4      15         4          0    132484
29677742      15         4      16         3          0    132484
29677743      16         3      17         4          0    132484
29677744      17         4      18         4          0    132484
29677745      18         4       1         2          0    132484

[29677746 rows x 6 columns]

In [11]:
unique_type_relations = edge_details_df.groupby(['src_type', 'dst_type'])[['trace_id']].count().reset_index()
unique_type_relations

src_type  dst_type  trace_id
0          0         1    825724
1          0         2      2257
2          0         4   1247876
3          0         5    756592
4          1         0   2699666
5          1         1    154545
6          1         3   1474923
7          1         4   1031469
8          1         5     50000
9          1         6       407
10         2         3   2699666
11         3         1    216097
12         3         2    770683
13         3         3     79799
14         3         4   1625613
15         3         5     18900
16         3         6       252
17         4         1   1272885
18         4         2   1302083
19         4         3   1121381
20         4         4   2030502
21         4         5   1345960
22         4         6     19367
23         5         1    242093
24         5         2    818654
25         5         3     26799
26         5         4   1087153
27         5         5   6555221
28         5         6     10498
29         6         2      1976
30         6         3      8442
31         6         4     17867
32         6         5      2239
33         6         6     33749
34         6         7     63204
35         7         4     51698
36         7         5     11506

In [15]:
relation_neigh_df = edge_details_df.groupby(['trace_id', 'src_type', 'dst_type', 'src_id']).agg(
    {
        'dst_id': lambda x: x.tolist()
    }
).reset_index()

relation_neigh_df

trace_id  src_type  dst_type  src_id dst_id
0                0         0         1      74   [76]
1                0         0         1      79   [81]
2                0         0         1      89   [91]
3                0         0         1      94   [96]
4                0         0         1     112  [114]
...            ...       ...       ...     ...    ...
29674617    132484         4         4      12   [13]
29674618    132484         4         4      13   [14]
29674619    132484         4         4      14   [15]
29674620    132484         4         4      17   [18]
29674621    132484         5         4       2    [3]

[29674622 rows x 5 columns]

In [46]:
relation_neigh_df['dst_id'].apply(lambda x: len(x)).max()

2

In [28]:
relation_neigh_df['dst_id_list'] = relation_neigh_df['dst_id'].apply(lambda x: ','.join([str(i) for i in x]))
relation_neigh_df

trace_id  src_type  dst_type  src_id dst_id dst_id_list
0                0         0         1      74   [76]          76
1                0         0         1      79   [81]          81
2                0         0         1      89   [91]          91
3                0         0         1      94   [96]          96
4                0         0         1     112  [114]         114
...            ...       ...       ...     ...    ...         ...
29674617    132484         4         4      12   [13]          13
29674618    132484         4         4      13   [14]          14
29674619    132484         4         4      14   [15]          15
29674620    132484         4         4      17   [18]          18
29674621    132484         5         4       2    [3]           3

[29674622 rows x 6 columns]

In [31]:
for src_type, dst_type in unique_type_relations[['src_type', 'dst_type']].values:
    print(f'Processing {src_type}_{dst_type}')
    cond = (relation_neigh_df['src_type'] == src_type) & (relation_neigh_df['dst_type'] == dst_type)
    relation_neigh_df[['trace_id', 'src_id', 'dst_id_list']][cond].to_csv(f'{output_root_dir}/{src_type}_{dst_type}_list.txt', sep=':', index=None, header=False)


Processing 0_1
Processing 0_2
Processing 0_4
Processing 0_5
Processing 1_0
Processing 1_1
Processing 1_3
Processing 1_4
Processing 1_5
Processing 1_6
Processing 2_3
Processing 3_1
Processing 3_2
Processing 3_3
Processing 3_4
Processing 3_5
Processing 3_6
Processing 4_1
Processing 4_2
Processing 4_3
Processing 4_4
Processing 4_5
Processing 4_6
Processing 5_1
Processing 5_2
Processing 5_3
Processing 5_4
Processing 5_5
Processing 5_6
Processing 6_2
Processing 6_3
Processing 6_4
Processing 6_5
Processing 6_6
Processing 6_7
Processing 7_4
Processing 7_5


### Get Incoming Edge Embedding

In [32]:
edge_details_df

src_id  src_type  dst_id  dst_type  edge_type  trace_id
0              0         0       2         4          0         0
1              2         4       3         1          0         0
2              3         1       4         1          0         0
3              4         1       5         3          0         0
4              5         3       6         4          0         0
...          ...       ...     ...       ...        ...       ...
29677741      14         4      15         4          0    132484
29677742      15         4      16         3          0    132484
29677743      16         3      17         4          0    132484
29677744      17         4      18         4          0    132484
29677745      18         4       1         2          0    132484

[29677746 rows x 6 columns]

In [36]:
incoming_edge_embeddings = pd.get_dummies(
    edge_details_df.drop(['src_type', 'src_id'], axis=1),
    columns=['edge_type'],
    prefix='e'
)

incoming_edge_embeddings


dst_id  dst_type  trace_id  e_0  e_1  e_2  e_3
0              2         4         0    1    0    0    0
1              3         1         0    1    0    0    0
2              4         1         0    1    0    0    0
3              5         3         0    1    0    0    0
4              6         4         0    1    0    0    0
...          ...       ...       ...  ...  ...  ...  ...
29677741      15         4    132484    1    0    0    0
29677742      16         3    132484    1    0    0    0
29677743      17         4    132484    1    0    0    0
29677744      18         4    132484    1    0    0    0
29677745       1         2    132484    1    0    0    0

[29677746 rows x 7 columns]

In [38]:
incoming_edge_embeddings.drop('dst_type', axis=1).groupby(['trace_id', 'dst_id']).sum().reset_index() \
    .to_csv(f'{output_root_dir}/incoming_edge_embedding.csv', index=False)

In [45]:
import os 
sorted(os.listdir('../HetGNN/ProcessedData'))

['0_1_list.txt',
 '0_2_list.txt',
 '0_4_list.txt',
 '0_5_list.txt',
 '1_0_list.txt',
 '1_1_list.txt',
 '1_3_list.txt',
 '1_4_list.txt',
 '1_5_list.txt',
 '1_6_list.txt',
 '2_3_list.txt',
 '3_1_list.txt',
 '3_2_list.txt',
 '3_3_list.txt',
 '3_4_list.txt',
 '3_5_list.txt',
 '3_6_list.txt',
 '4_1_list.txt',
 '4_2_list.txt',
 '4_3_list.txt',
 '4_4_list.txt',
 '4_5_list.txt',
 '4_6_list.txt',
 '5_1_list.txt',
 '5_2_list.txt',
 '5_3_list.txt',
 '5_4_list.txt',
 '5_5_list.txt',
 '5_6_list.txt',
 '6_2_list.txt',
 '6_3_list.txt',
 '6_4_list.txt',
 '6_5_list.txt',
 '6_6_list.txt',
 '6_7_list.txt',
 '7_4_list.txt',
 '7_5_list.txt',
 'incoming_edge_embedding.csv',
 'trace_id_idx.json']

In [66]:
trace_info_df = pd.read_csv(f'../HetGNN/ProcessedData/trace_info.csv', index_col=None)
trace_info_df

trace_id  trace_bool error_trace_type  process_idx
0              0        True           normal            0
1              1        True           normal            0
2              2        True           normal            0
3              3        True           normal            0
4              4        True           normal            0
...          ...         ...              ...          ...
132480    132480       False           F04-02            8
132481    132481       False           F04-02            8
132482    132482       False           F04-02            8
132483    132483       False           F04-02            8
132484    132484       False           F04-02            8

[132485 rows x 4 columns]

In [78]:
trace_info_df[trace_info_df['trace_bool']==True]

trace_id  trace_bool error_trace_type  process_idx
0              0        True           normal            0
1              1        True           normal            0
2              2        True           normal            0
3              3        True           normal            0
4              4        True           normal            0
...          ...         ...              ...          ...
132440    132440        True           normal            8
132441    132441        True           normal            8
132442    132442        True           normal            8
132443    132443        True           normal            8
132444    132444        True           normal            8

[109151 rows x 4 columns]

In [87]:
trace_info_df[trace_info_df['trace_id'].isin([1,2])]['trace_bool'].apply(lambda x: 0 if x else 1)

1    0
2    0
Name: trace_bool, dtype: int64

## Using Node Attr embedding

In [91]:
import json
node_embedding = defaultdict(list)
for idx in range(0, 9):
    with open(f'{graph_data_path_root}/process{idx}.jsons', 'r') as fin:
        for line in tqdm(fin.readlines()):
            trace = json.loads(line)
            node_info = trace['node_info']
            for i, vector in enumerate(node_info):
                node_embedding['trace_id'].append(trace['trace_id'])
                node_embedding['node_id'].append(i)
                for j, attr in enumerate(vector):
                    node_embedding[f'node_attr_{j}'].append(attr)
node_embedding_df = pd.DataFrame(node_embedding)
node_embedding_df

100%|██████████| 14719/14719 [00:12<00:00, 1179.82it/s]


trace_id  node_id  \
0         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...        0   
1         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...        1   
2         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...        2   
3         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...        3   
4         007efb9578bc4f1ab3eab03cb5188af5.38.1629255886...        4   
...                                                     ...      ...   
27110858  ffc3e79734424b65942466e0d8d432e2.47.1628705868...       14   
27110859  ffc3e79734424b65942466e0d8d432e2.47.1628705868...       15   
27110860  ffc3e79734424b65942466e0d8d432e2.47.1628705868...       16   
27110861  ffc3e79734424b65942466e0d8d432e2.47.1628705868...       17   
27110862  ffc3e79734424b65942466e0d8d432e2.47.1628705868...       18   

          node_attr_0  node_attr_1  node_attr_2  node_attr_3  node_attr_4  \
0              1460.0         13.0           -1          0.0            0   
1              1460.0         13.0           -1        922.0            2   
2               502.0         13.0           -1          2.0            4   
3              1364.0         13.0           13          3.0            1   
4              1364.0         13.0           13         10.0            1   
...               ...          ...          ...          ...          ...   
27110858        973.0         30.0           -1          2.0            4   
27110859        958.0         30.0           -1          2.0            4   
27110860       1496.0         30.0           30          3.0            3   
27110861       1004.0         30.0           -1          3.0            4   
27110862       1004.0         30.0           -1          3.0            4   

          node_attr_5  node_attr_6  
0                 0.0         1666  
1                 0.0         1667  
2                 0.0          502  
3                 1.0         1375  
4                 2.0         1375  
...               ...          ...  
27110858          0.0          973  
27110859          0.0          958  
27110860          2.0         1813  
27110861          0.0         1004  
27110862          0.0         1004  

[27110863 rows x 9 columns]

In [92]:
node_embedding_df['trace_id'] = node_embedding_df['trace_id'].apply(lambda x: trace_id_idx[x])
node_embedding_df

trace_id  node_id  node_attr_0  node_attr_1  node_attr_2  \
0                0        0       1460.0         13.0           -1   
1                0        1       1460.0         13.0           -1   
2                0        2        502.0         13.0           -1   
3                0        3       1364.0         13.0           13   
4                0        4       1364.0         13.0           13   
...            ...      ...          ...          ...          ...   
27110858    132484       14        973.0         30.0           -1   
27110859    132484       15        958.0         30.0           -1   
27110860    132484       16       1496.0         30.0           30   
27110861    132484       17       1004.0         30.0           -1   
27110862    132484       18       1004.0         30.0           -1   

          node_attr_3  node_attr_4  node_attr_5  node_attr_6  
0                 0.0            0          0.0         1666  
1               922.0            2          0.0         1667  
2                 2.0            4          0.0          502  
3                 3.0            1          1.0         1375  
4                10.0            1          2.0         1375  
...               ...          ...          ...          ...  
27110858          2.0            4          0.0          973  
27110859          2.0            4          0.0          958  
27110860          3.0            3          2.0         1813  
27110861          3.0            4          0.0         1004  
27110862          3.0            4          0.0         1004  

[27110863 rows x 9 columns]

In [95]:
node_embedding_df.to_csv(f'{output_root_dir}/node_embedding.csv', index=False)

## Random Walk to Find Neighbours